In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from statsmodels.tsa.arima.model import ARIMA
from sklearn.metrics import f1_score, accuracy_score, recall_score, precision_score

# Load the dataset
t = pd.read_csv(r"C:\Users\kanik\Desktop\TimeSeriesAnomalyDetection\data_2025.csv")
t["timestamp"] = pd.to_datetime(t["timestamp"])

# Set the anomaly column to identify the normal data (anomaly = 0)
train_dataset = t[:365 * 24 * 60]  # 1 year of data
train_dataset = train_dataset[train_dataset["anomaly"] == 0]  # only take normal data for forecasting training

# Variables for analysis
variables = ['temperature', 'pressure', 'power']
sample_size = 10000  # Use the first 10,000 samples for plotting and analysis

# Train-Test Split
train_size = int(len(train_dataset) * 0.8)  # 80% for training, 20% for testing
train_data = train_dataset[:train_size]
test_data = train_dataset[train_size:]

# Define the ARIMA model
def arima_forecast(data, p, d, q):
    try:
        model = ARIMA(data, order=(p, d, q))  # ARIMA model
        model_fit = model.fit()  # Fit the model
        forecast = model_fit.forecast(steps=1)  # Forecast the next time step
        return forecast
    except Exception as e:
        print(f"Error during forecast: {e}")
        return None

# Initialize forecast_results with empty lists for each variable
forecast_results = {var: [] for var in variables}

# Forecasting for each variable
for var in variables:
    train_series = train_data[var]

    # Train the ARIMA model for each feature and forecast
    for i in range(len(train_series)-1):
        train_series_data = train_series[:i+1]  # Training data up to the current timestamp
        forecast = arima_forecast(train_series_data, p=2, d=1, q=1)  # ARIMA(2,1,1) as an example
        
        if forecast is not None:
            print(f"Forecast for {var} at index {i}: {forecast}")  # Debugging print
            # Fix: Access the forecast value correctly - it's a pandas Series
            forecast_value = forecast.iloc[0] if isinstance(forecast, pd.Series) else forecast
            forecast_results[var].append(forecast_value)
        else:
            print(f"Forecast failed for {var} at index {i}")

# Convert forecast results into DataFrame for plotting
forecast_df = pd.DataFrame(forecast_results)
forecast_df['timestamp'] = train_data['timestamp'][1:].reset_index(drop=True)

# Plot the forecasted values alongside the actual data for the training set
fig, axs = plt.subplots(3, 1, figsize=(20, 10), sharex=True)
for i, var in enumerate(variables):
    axs[i].plot(train_data["timestamp"][1:], train_data[var][1:], label=f'Actual {var}', color='blue')
    axs[i].plot(forecast_df["timestamp"], forecast_df[var], label=f'Forecasted {var}', color='red')
    axs[i].set_title(f'{var} Forecasting using ARIMA (Training Set)')
    axs[i].set_ylabel('Value')
    axs[i].legend()

plt.tight_layout()
plt.show()

# Create forecast for test data - this part appears to be incomplete in the original
# First, ensure we have forecast_df_test defined
forecast_results_test = {var: [] for var in variables}

# For simplicity, assume we're using the same model for test forecasting
for var in variables:
    test_series = test_data[var]
    
    for i in range(len(test_series)-1):
        test_series_data = test_series[:i+1]
        forecast = arima_forecast(test_series_data, p=2, d=1, q=1)
        
        if forecast is not None:
            forecast_value = forecast.iloc[0] if isinstance(forecast, pd.Series) else forecast
            forecast_results_test[var].append(forecast_value)
        else:
            # Handle failed forecasts by using the previous value or a default
            if i > 0:
                forecast_results_test[var].append(test_series.iloc[i])
            else:
                forecast_results_test[var].append(test_series.iloc[0])

# Convert test forecast results into DataFrame
forecast_df_test = pd.DataFrame(forecast_results_test)
forecast_df_test['timestamp'] = test_data['timestamp'][1:].reset_index(drop=True)

# Calculate errors between forecast and ground truth
forecast_errors = np.abs(test_data[variables].iloc[1:].values - forecast_df_test[variables].values)

# Set thresholds to detect anomalies
temp_threshold = 1
pres_threshold = 0.06
powe_threshold = 2.75

# Detect anomalies based on error thresholds
detected_anomaly = (forecast_errors > np.array([temp_threshold, pres_threshold, powe_threshold])).any(axis=1)

# Ground truth anomalies from the dataset (from test set)
test_ground_truth_anomalies = (test_data["anomaly"].iloc[1:] > 0).values

# Evaluate the model's performance using F1 score, accuracy, precision, and recall
f1 = f1_score(test_ground_truth_anomalies, detected_anomaly)
accuracy = accuracy_score(test_ground_truth_anomalies, detected_anomaly)
precision = precision_score(test_ground_truth_anomalies, detected_anomaly)
recall = recall_score(test_ground_truth_anomalies, detected_anomaly)

print(f"Test Set - Accuracy: {accuracy:.3f}")
print(f"Test Set - Precision: {precision:.3f}")
print(f"Test Set - Recall: {recall:.3f}")
print(f"Test Set - F1-score: {f1:.3f}")

c:\Users\kanik\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:866: UserWarning: Too few observations to estimate starting parameters for ARMA and trend. All parameters except for variances will be set to zeros.
  warn('Too few observations to estimate starting parameters%s.'
c:\Users\kanik\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\tsa\statespace\mlemodel.py:1235: RuntimeWarning: invalid value encountered in divide
  np.inner(score_obs, score_obs) /
c:\Users\kanik\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:866: UserWarning: Too few observations to estimate starting parameters for ARMA and trend. All parameters except for variances will be set to zeros.
  warn('Too few observations to estimate starting parameters%s.'
c:\Users\kanik\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:866: UserWarning: Too few observat

Forecast for temperature at index 0: 1    15.14935
dtype: float64
Error during forecast: too many indices for array: array is 0-dimensional, but 1 were indexed
Forecast failed for temperature at index 1
Forecast for temperature at index 2: 3    14.97079
dtype: float64
Forecast for temperature at index 3: 4    15.025364
dtype: float64
Forecast for temperature at index 4: 5    14.966339
dtype: float64
Forecast for temperature at index 5: 6    15.129099
dtype: float64


c:\Users\kanik\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
c:\Users\kanik\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
c:\Users\kanik\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\base\model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "


Forecast for temperature at index 6: 7    15.04104
dtype: float64
Forecast for temperature at index 7: 8    15.184241
dtype: float64
Forecast for temperature at index 8: 9    15.031857
dtype: float64
Forecast for temperature at index 9: 10    15.072282
dtype: float64


c:\Users\kanik\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
c:\Users\kanik\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\base\model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
c:\Users\kanik\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:966: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
c:\Users\kanik\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\tsa\statespace\sarimax.py:978: UserWarning: Non-invertible starting MA parameters found. Using zer

...

Forecast for temperature at index 4003: 4004    18.729195
dtype: float64


c:\Users\kanik\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\tsa\base\tsa_model.py:837: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
c:\Users\kanik\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\tsa\base\tsa_model.py:837: FutureWarning: No supported index is available. In the next version, calling this method in a model without a supported index will result in an exception.
  return get_prediction_index(
c:\Users\kanik\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: An unsupported index was provided. As a result, forecasts cannot be generated. To use the model for forecasting, use one of the supported classes of index.
  self._init_dates(dates, freq)
c:\Users\kanik\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarn

Forecast for temperature at index 4004: 4005    18.699462
dtype: float64


c:\Users\kanik\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\tsa\base\tsa_model.py:837: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
c:\Users\kanik\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\tsa\base\tsa_model.py:837: FutureWarning: No supported index is available. In the next version, calling this method in a model without a supported index will result in an exception.
  return get_prediction_index(
c:\Users\kanik\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarning: An unsupported index was provided. As a result, forecasts cannot be generated. To use the model for forecasting, use one of the supported classes of index.
  self._init_dates(dates, freq)
c:\Users\kanik\AppData\Local\Programs\Python\Python310\lib\site-packages\statsmodels\tsa\base\tsa_model.py:473: ValueWarn

Forecast for temperature at index 4005: 4006    18.718349
dtype: float64
